In [111]:
import glob
import requests as r
import bs4
import regex as re
from tqdm import tqdm

In [15]:
base_url = "https://www.dansketaler.dk/soeg?q=%2A&sort=date&page={}"

In [75]:
search_res = r.get(base_url.format(1))

In [76]:
bs = bs4.BeautifulSoup(search_res.content)

In [77]:
speeches = bs.find_all("div", attrs={"class": "speech-hit"})

In [67]:
speeches[-1].find_all("span", attrs={"class": "genre"})

[<span class="genre" itemprop="keywords" title="Talegenre">Prædiken</span>]

In [97]:
speech_links = []
start = 1
for i in range(start, 1000):
    search_res = r.get(base_url.format(i))
    bs = bs4.BeautifulSoup(search_res.content)
    speeches = bs.find_all("div", attrs={"class": "speech-hit"})
    if speeches == []:
        break
    for speech in speeches:
        title = speech.find("div", attrs={"class", "speech-title"}).get_text()
        if len(speech.find_all("span", attrs={"class": "genre"})) > 0:
            if speech.find("span", attrs={"class": "genre"}).get_text() == "Prædiken":
                continue
        link = speech.find("a", attrs={"class", "special"})["href"]
        speech_links.append((title,link))
    

In [104]:
title, link = speech_links[3]

In [105]:
BASE = "https://www.dansketaler.dk"
link = f"{BASE}{link}"
link

'https://www.dansketaler.dk/tale/victoria-birks-tale-ved-arrangementet-oprab-unge-tager-ordet-i-operaen'

In [123]:
BASE = "https://www.dansketaler.dk"

with tqdm(total = len(speech_links[1298:]), desc="Processing Files") as fpbar:
    for link in speech_links[1298:]:
        title, link = link
        link = f"{BASE}{link}"

        res = r.get(link)
        bs = bs4.BeautifulSoup(res.content)
        if bs.find("div", attrs={"class", "speech-article-content"}) is None:
            continue
        speech_text = bs.find("div", attrs={"class", "speech-article-content"}).get_text("\n")
        file_name = f"taler/{title.replace(" ", "_").replace("/","")}.txt"
        with open(file_name, "w") as f:
            f.write(speech_text)
        fpbar.update(1)

Processing Files: 100%|█████████▉| 2615/2625 [06:32<00:01,  6.66it/s]


In [120]:
speech_links[1297]

('Pia Olsen Dyhrs tale ved udvidet partilederdebat',
 '/tale/pia-olsen-dyhrs-tale-ved-udvidet-partilederdebat')

In [ ]:

files = glob.glob("*", root_dir="taler")
all_lines = []
for file_name in glob.glob("*", root_dir="taler"):
    speech_name = file_name.replace(".txt", "")
    with open(f"taler/{file_name}", "r") as f: 
        all_lines.extend(f.readlines())
all_lines = list(filter(lambda l: (re.search('[a-zA-Z]', l) is not None), all_lines))
all_lines = [line.replace("\n", "") for line in all_lines]

with open("taler.txt", "a") as f:
    for line in all_lines:
        f.write(f"{line}\n")

In [3]:
import json

from llama_index.core import SimpleDirectoryReader
from llama_index.core.node_parser import SentenceSplitter
from llama_index.core.schema import MetadataMode

In [29]:
!mkdir -p 'data/10k/'
!curl 'https://raw.githubusercontent.com/run-llama/llama_index/main/docs/docs/examples/data/10k/uber_2021.pdf' -O 'data/10k/uber_2021.pdf'
!curl 'https://raw.githubusercontent.com/run-llama/llama_index/main/docs/docs/examples/data/10k/lyft_2021.pdf' -O 'data/10k/lyft_2021.pdf'

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 1836k  100 1836k    0     0  4456k      0 --:--:-- --:--:-- --:--:-- 4457k
curl: (6) Could not resolve host: data
  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 1406k  100 1406k    0     0  3894k      0 --:--:-- --:--:-- --:--:-- 3896k
curl: (6) Could not resolve host: data


In [30]:

TRAIN_FILES = ["./data/10k/lyft_2021.pdf"]
VAL_FILES = ["./data/10k/uber_2021.pdf"]

TRAIN_CORPUS_FPATH = "./data/train_corpus.json"
VAL_CORPUS_FPATH = "./data/val_corpus.json"

In [5]:
def load_corpus(files, verbose=False):
    if verbose:
        print(f"Loading files {files}")

    reader = SimpleDirectoryReader(input_files=files)
    docs = reader.load_data()
    if verbose:
        print(f"Loaded {len(docs)} docs")

    parser = SentenceSplitter()
    nodes = parser.get_nodes_from_documents(docs, show_progress=verbose)

    if verbose:
        print(f"Parsed {len(nodes)} nodes")

    return nodes

In [7]:
train_nodes = load_corpus(["./taler.txt"], verbose=True)

Loading files ['./taler.txt']
Loaded 1 docs


Parsing nodes:   0%|          | 0/1 [00:00<?, ?it/s]

Parsed 639 nodes


In [8]:
train_nodes

[TextNode(id_='4c0cdc28-b426-4353-ad18-6780793b482b', embedding=None, metadata={'file_path': 'taler.txt', 'file_name': 'taler.txt', 'file_type': 'text/plain', 'file_size': 1581868, 'creation_date': '2025-02-10', 'last_modified_date': '2025-02-10'}, excluded_embed_metadata_keys=['file_name', 'file_type', 'file_size', 'creation_date', 'last_modified_date', 'last_accessed_date'], excluded_llm_metadata_keys=['file_name', 'file_type', 'file_size', 'creation_date', 'last_modified_date', 'last_accessed_date'], relationships={<NodeRelationship.SOURCE: '1'>: RelatedNodeInfo(node_id='2ff40e8d-ea6b-4430-8c41-641befd44627', node_type=<ObjectType.DOCUMENT: '4'>, metadata={'file_path': 'taler.txt', 'file_name': 'taler.txt', 'file_type': 'text/plain', 'file_size': 1581868, 'creation_date': '2025-02-10', 'last_modified_date': '2025-02-10'}, hash='dac66003c193c8f1413365f94d4540310e2ca16431e4c35e6bdb90e38c355485'), <NodeRelationship.NEXT: '3'>: RelatedNodeInfo(node_id='9360c77b-af55-4fb8-9b88-31c52814ac

In [42]:
val_nodes

[TextNode(id_='5ed6f639-eebb-45fe-9407-114cfa5ac7c1', embedding=None, metadata={'page_label': '1', 'file_name': 'uber_2021.pdf', 'file_path': 'data/10k/uber_2021.pdf', 'file_type': 'application/pdf', 'file_size': 1880483, 'creation_date': '2025-02-10', 'last_modified_date': '2025-02-10'}, excluded_embed_metadata_keys=['file_name', 'file_type', 'file_size', 'creation_date', 'last_modified_date', 'last_accessed_date'], excluded_llm_metadata_keys=['file_name', 'file_type', 'file_size', 'creation_date', 'last_modified_date', 'last_accessed_date'], relationships={<NodeRelationship.SOURCE: '1'>: RelatedNodeInfo(node_id='b4192afb-0306-443e-8493-f34fa861a841', node_type=<ObjectType.DOCUMENT: '4'>, metadata={'page_label': '1', 'file_name': 'uber_2021.pdf', 'file_path': 'data/10k/uber_2021.pdf', 'file_type': 'application/pdf', 'file_size': 1880483, 'creation_date': '2025-02-10', 'last_modified_date': '2025-02-10'}, hash='2646fbb691963b881c755e842a522a5d366496991015049fcde9c3147127b9df')}, metada

In [ ]:
res = r.get("https://www.dansketaler.dk/tale/victoria-birks-tale-ved-arrangementet-oprab-unge-tager-ordet-i-operaen")
bs = bs4.BeautifulSoup(res.content)
bs.find("div", attrs={"class", "speech-article-content"}).get_text("\n")

'\n\nKald sig selv for feminist \nPause \nJeg er feminist \nJeg er en politisk korrekt og krænkelsesparat fribløder \nlille pause \neller det tror nogen når jeg fortæller dem, at jeg er en del feministklubben \nsammen med alle de andre \nrød-strømpe-bærende hekse \nmed hår alle vegne - på vores seksuel frigjorte kroppe, fordi vi smed bh’en i en strøg aktion\nos vrede søstre med skingrende højtråbende stemmer \nPause\nEj men er det ikke på tide, at vi i 2025 holder op med at have så stereotype billeder på hvordan en feminist ser ud\nog at vi I 2025 holder med at være så skide bange for det feminine så vi kan gøre op med at kampen for ligestilling kun handler om kvinder for det handler i virkeligheden om alle mennesker, uanset køn, klasse, etnicitet, seksualitet, handicap osv. \nDet handler om opgøret med de \npatriarkalske magtstrukturer!!!\n der er i vores samfund,\xa0\nog derfor er det så pisse vigtigt, at den her kamp, stadig hedder feminisme\xa0\nSå kald dig selv for feminist!\xa0\n

In [109]:
bs

<!DOCTYPE html>
<html lang="da">
<head>
<title>Victoria Birks tale ved arrangementet “Opråb! Unge tager ordet i Operaen”</title>
<meta name="description"/>
<meta content="width=device-width, initial-scale=1" name="viewport"/>
<meta content="/msg/cookie-popup" name="site-msg"/>
<meta content="Victoria Birks tale ved arrangementet “Opråb! Unge tager ordet i Operaen”" property="og:title"/>
<meta content="website" property="og:type"/>
<meta content="https://www.dansketaler.dk/tale/victoria-birks-tale-ved-arrangementet-oprab-unge-tager-ordet-i-operaen" property="og:url"/>
<meta content="" property="og:description"/>
<meta content="https://www.dansketaler.dk/storage/representations/proxy/eyJfcmFpbHMiOnsiZGF0YSI6MTQ5NTYsInB1ciI6ImJsb2JfaWQifX0=--d083c36d52eccb1d5c1ff668d6c18037cc456e1f/eyJfcmFpbHMiOnsiZGF0YSI6eyJmb3JtYXQiOiJqcGciLCJyZXNpemVfdG9fZmlsbCI6WzEyMDAsMTIwMF19LCJwdXIiOiJ2YXJpYXRpb24ifX0=--894c9113aff9e979bca9bf5f5e3676abda5a0415/og_image.jpg" property="og:image"/>
<link href="/favico